In [4]:
import pandas as pd
import numpy as np
import pickle
from textblob import TextBlob
import torch

from sklearn.model_selection import train_test_split
from sklearn import linear_model
from sklearn import metrics
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics.pairwise import cosine_similarity

import numpy as np
from numpy import dot
from numpy.linalg import norm
from sklearn.externals import joblib

import warnings
warnings.filterwarnings('ignore')

ModuleNotFoundError: No module named 'torch'

In [ ]:
!pip install torch --user

  Using cached https://files.pythonhosted.org/packages/24/19/4804aea17cd136f1705a5e98a00618cb8f6ccc375ad8bfa437408e09d058/torch-1.4.0-cp36-cp36m-manylinux1_x86_64.whl


# Dowload Nltk Data

In [2]:
import nltk
nltk.download('punkt')

[nltk_data] Downloading package punkt to /Users/rajatjain/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

# Load Infersent Pre-trained Model

In [7]:
from InferSent.models import InferSent
V = 1
MODEL_PATH = './encoder/infersent%s.pkl' % V
params_model = {'bsize': 64, 'word_emb_dim': 300, 'enc_lstm_dim': 2048,
                'pool_type': 'max', 'dpout_model': 0.0, 'version': V}
infersent = InferSent(params_model)
infersent.load_state_dict(torch.load(MODEL_PATH))
W2V_PATH = './Glove/glove.840B.300d.txt'
infersent.set_w2v_path(W2V_PATH)

# Read Data

In [8]:
train = pd.read_json('./data/train-v1.1.json')

In [9]:
contexts = []
questions = []
answers = []
titles = []

def get_attributes(item):
    data = item['data']
    title = data['title']
    for paragraph in data['paragraphs']:
        for qas in paragraph['qas']:
            answers.append(qas['answers'][0]['text'])
            questions.append(qas['question'])
            contexts.append(paragraph['context'])
            titles.append(title)
            
def build_dataframe(train):
    train.apply(get_attributes, axis = 1)
    train_df = pd.DataFrame({
    'contexts':contexts,
    'questions': questions,
    'answers': answers,
    'titles': titles
})
    return train_df
    
train_df = build_dataframe(train)
train_df = train_df.head(5000)

In [10]:
train_df.shape

(5000, 4)

# Split Paragraph into Sentences

In [11]:
train_df['sentences'] = train_df['contexts'].apply(lambda x : [item.raw for item in TextBlob(x).sentences ])

# Get Target

In [12]:
def get_target(item):
    """ Builds the target using the index number of answer in the list of sentences
    """
    for index, sentence in enumerate( item['sentences']):
        if item['answers'] in sentence:
            return index
    return 0
    
train_df['target'] = train_df.apply(get_target, axis = 1)

In [13]:
def get_all_sentences(sentences):
    all_sentences = []
    sentences = sentences.tolist()
    for context_sentences in sentences:
        for setence in context_sentences:
            all_sentences.append(setence)
        
    all_sentences = list(dict.fromkeys(all_sentences))
    return all_sentences

# Generate Vocab

In [14]:
paras = list(train_df["contexts"].drop_duplicates().reset_index(drop= True))
blob = TextBlob(" ".join(paras))
sentences = get_all_sentences(train_df['sentences'])
infersent.build_vocab(sentences, tokenize=True)

Found 14620(/15387) words with w2v vectors
Vocab size : 14620


# Build Embeddings

In [15]:
# Sentence Embeddings
dict_embeddings = {}
for i in range(len(sentences)):
    dict_embeddings[sentences[i]] = infersent.encode([sentences[i]], tokenize=True)[0]
  
# Question Embeddings
questions = list(train_df["questions"])    
for i in range(len(questions)):
    dict_embeddings[questions[i]] = infersent.encode([questions[i]], tokenize=True)[0]
    

# Save Embeddings

In [156]:
# Todo
# This will help to save the computation time

In [157]:
def get_context_embeddings(item):
    embeddings = []
    for sentence in item.sentences:
        embeddings.append(dict_embeddings[sentence])
    return embeddings

In [158]:
train_df['question_embedding'] = train_df['questions'].apply(lambda x : dict_embeddings[x])
train_df['context_embedding'] = train_df.apply(get_context_embeddings, axis = 1)

In [159]:
train_df.head()

contexts  \
0  Architecturally, the school has a Catholic cha...   
1  Architecturally, the school has a Catholic cha...   
2  Architecturally, the school has a Catholic cha...   
3  Architecturally, the school has a Catholic cha...   
4  Architecturally, the school has a Catholic cha...   

                                           questions  \
0  To whom did the Virgin Mary allegedly appear i...   
1  What is in front of the Notre Dame Main Building?   
2  The Basilica of the Sacred heart at Notre Dame...   
3                  What is the Grotto at Notre Dame?   
4  What sits on top of the Main Building at Notre...   

                                   answers                    titles  \
0               Saint Bernadette Soubirous  University_of_Notre_Dame   
1                a copper statue of Christ  University_of_Notre_Dame   
2                        the Main Building  University_of_Notre_Dame   
3  a Marian place of prayer and reflection  University_of_Notre_Dame   
4       a golden statue of the Virgin Mary  University_of_Notre_Dame   

                                           sentences  target  \
0  [Architecturally, the school has a Catholic ch...       5   
1  [Architecturally, the school has a Catholic ch...       2   
2  [Architecturally, the school has a Catholic ch...       1   
3  [Architecturally, the school has a Catholic ch...       4   
4  [Architecturally, the school has a Catholic ch...       1   

                                  question_embedding  \
0  [0.11010079, 0.11422938, 0.11560896, 0.0548947...   
1  [0.10951652, 0.11030624, 0.052100062, 0.030539...   
2  [0.011956477, 0.14930709, 0.028481212, 0.05278...   
3  [0.07114332, 0.054118324, -0.0139598325, 0.053...   
4  [0.16131133, 0.15654244, 0.08214854, 0.0437286...   

                                   context_embedding  
0  [[0.055199962, 0.0501314, 0.04787037, 0.016248...  
1  [[0.055199962, 0.0501314, 0.04787037, 0.016248...  
2  [[0.055199962, 0.0501314, 0.04787037, 0.016248...  
3  [[0.055199962, 0.0501314, 0.04787037, 0.016248...  
4  [[0.055199962, 0.0501314, 0.04787037, 0.016248...

# Generate Features

In [160]:
from sklearn.metrics.pairwise import euclidean_distances

In [161]:
def get_metric(item, metric):
    result = []
    for i in range(0,len(item.sentences)):
        question_embedding = [item.question_embedding]
        sentence_embedding = [item['context_embedding'][i]]

        if metric == 'cosine_similarity':
            metric = cosine_similarity(question_embedding, sentence_embedding)
            
        if metric == 'euclidean':
            metric = euclidean_distances(question_embedding, sentence_embedding)  

        result.append(metric[0][0])  
    return result
    

In [162]:
train_df['cosine_similarity'] = train_df.apply(lambda item : get_metric(item, 'cosine_similarity'), axis = 1)
train_df['euclidean'] = train_df.apply(lambda item : get_metric(item, 'euclidean'), axis = 1)

/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:10: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  # Remove the CWD from sys.path while we load stuff.
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:7: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  import sys
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:10: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  # Remove the CWD from sys.path while we load stuff.
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:7: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  imp

/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:10: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  # Remove the CWD from sys.path while we load stuff.
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:7: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  import sys
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:10: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  # Remove the CWD from sys.path while we load stuff.
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:7: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  imp

/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:10: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  # Remove the CWD from sys.path while we load stuff.
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:7: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  import sys
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:10: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  # Remove the CWD from sys.path while we load stuff.
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:7: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  imp

/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:10: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  # Remove the CWD from sys.path while we load stuff.
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:7: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  import sys
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:10: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  # Remove the CWD from sys.path while we load stuff.
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:7: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  imp

/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:10: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  # Remove the CWD from sys.path while we load stuff.
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:7: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  import sys
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:10: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  # Remove the CWD from sys.path while we load stuff.
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:7: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  imp

...

/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:7: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  import sys
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:10: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  # Remove the CWD from sys.path while we load stuff.
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:7: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  import sys
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:10: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  # Remove the CWD from sys.path while we load

/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:7: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  import sys
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:10: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  # Remove the CWD from sys.path while we load stuff.
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:7: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  import sys
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:10: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  # Remove the CWD from sys.path while we load

/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:7: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  import sys
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:10: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  # Remove the CWD from sys.path while we load stuff.
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:7: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  import sys
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:10: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  # Remove the CWD from sys.path while we load

/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:7: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  import sys
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:10: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  # Remove the CWD from sys.path while we load stuff.
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:7: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  import sys
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:10: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  # Remove the CWD from sys.path while we load

/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:7: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  import sys
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:10: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  # Remove the CWD from sys.path while we load stuff.
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:7: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  import sys
/Users/rajatjain/.pyenv/versions/3.6.6/lib/python3.6/site-packages/ipykernel_launcher.py:10: FutureWarning: elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison
  # Remove the CWD from sys.path while we load

In [163]:
train_df.head()

contexts  \
0  Architecturally, the school has a Catholic cha...   
1  Architecturally, the school has a Catholic cha...   
2  Architecturally, the school has a Catholic cha...   
3  Architecturally, the school has a Catholic cha...   
4  Architecturally, the school has a Catholic cha...   

                                           questions  \
0  To whom did the Virgin Mary allegedly appear i...   
1  What is in front of the Notre Dame Main Building?   
2  The Basilica of the Sacred heart at Notre Dame...   
3                  What is the Grotto at Notre Dame?   
4  What sits on top of the Main Building at Notre...   

                                   answers                    titles  \
0               Saint Bernadette Soubirous  University_of_Notre_Dame   
1                a copper statue of Christ  University_of_Notre_Dame   
2                        the Main Building  University_of_Notre_Dame   
3  a Marian place of prayer and reflection  University_of_Notre_Dame   
4       a golden statue of the Virgin Mary  University_of_Notre_Dame   

                                           sentences  target  \
0  [Architecturally, the school has a Catholic ch...       5   
1  [Architecturally, the school has a Catholic ch...       2   
2  [Architecturally, the school has a Catholic ch...       1   
3  [Architecturally, the school has a Catholic ch...       4   
4  [Architecturally, the school has a Catholic ch...       1   

                                  question_embedding  \
0  [0.11010079, 0.11422938, 0.11560896, 0.0548947...   
1  [0.10951652, 0.11030624, 0.052100062, 0.030539...   
2  [0.011956477, 0.14930709, 0.028481212, 0.05278...   
3  [0.07114332, 0.054118324, -0.0139598325, 0.053...   
4  [0.16131133, 0.15654244, 0.08214854, 0.0437286...   

                                   context_embedding  \
0  [[0.055199962, 0.0501314, 0.04787037, 0.016248...   
1  [[0.055199962, 0.0501314, 0.04787037, 0.016248...   
2  [[0.055199962, 0.0501314, 0.04787037, 0.016248...   
3  [[0.055199962, 0.0501314, 0.04787037, 0.016248...   
4  [[0.055199962, 0.0501314, 0.04787037, 0.016248...   

                                   cosine_similarity  \
0  [0.5752636, 0.5752636, 0.5752636, 0.5752636, 0...   
1  [0.5459254, 0.5459254, 0.5459254, 0.5459254, 0...   
2  [0.60825235, 0.60825235, 0.60825235, 0.6082523...   
3  [0.50993013, 0.50993013, 0.50993013, 0.5099301...   
4  [0.5222363, 0.5222363, 0.5222363, 0.5222363, 0...   

                                           euclidean  
0  [3.8162625, 3.8162625, 3.8162625, 3.8162625, 3...  
1  [3.590196, 3.590196, 3.590196, 3.590196, 3.590...  
2  [3.4122276, 3.4122276, 3.4122276, 3.4122276, 3...  
3  [3.6493201, 3.6493201, 3.6493201, 3.6493201, 3...  
4  [3.7629066, 3.7629066, 3.7629066, 3.7629066, 3...

In [164]:
train_df_copy = train_df.copy()

# Pad the euclidean and cosine_similarity features

In [165]:
def find_max_number_of_sentences():
    """
        finds the maximum number of sentences possible in any context
    """
    max_number_of_sentences = 0
    for i in range(0, train_df.shape[0]):
        length = len(train_df.iloc[i].sentences)
        if length > max_number_of_sentences:
            max_number_of_sentences = length  
    return max_number_of_sentences     
    
max_number_of_sentences = find_max_number_of_sentences()

In [175]:
max_number_of_sentences

22

In [166]:
def pad(data, max_length):
    mean = sum(data)/len(data)
    length_of_data = len(data)
    pad_number = max_length - length_of_data
    data = data + [mean]*pad_number
    return data
    

In [167]:
resultant_data = []
def combine_features(item):
    """
    Pads the euclidean and cosine values for particualr instance and generates resultant dataframe
    for modelling , it has eculidean distance between question and all sentnces and cosine similarity
    between between question and all sentences as well and last feature is the index of the answer in the sentnces
    """
    length_of_sentence = len(item.sentences)
    cosine_similarity = item.cosine_similarity
    euclidean = item.euclidean
    
    if length_of_sentence < max_number_of_sentences:
        euclidean = pad(euclidean, max_number_of_sentences)
        cosine_similarity = pad(cosine_similarity, max_number_of_sentences)
        
    features = euclidean + cosine_similarity + [item.target]    
    resultant_data.append(features)
train_df_copy.apply(combine_features, axis = 1)

resultant_data = pd.DataFrame(resultant_data)

In [174]:
resultant_data.head()

0         1         2         3         4         5         6   \
0  3.816262  3.816262  3.816262  3.816262  3.816262  3.816262  3.816262   
1  3.590196  3.590196  3.590196  3.590196  3.590196  3.590196  3.590196   
2  3.412228  3.412228  3.412228  3.412228  3.412228  3.412228  3.412228   
3  3.649320  3.649320  3.649320  3.649320  3.649320  3.649320  3.649320   
4  3.762907  3.762907  3.762907  3.762907  3.762907  3.762907  3.762907   

         7         8         9   ...        35        36        37        38  \
0  3.816262  3.816262  3.816262  ...  0.575264  0.575264  0.575264  0.575264   
1  3.590196  3.590196  3.590196  ...  0.545925  0.545925  0.545925  0.545925   
2  3.412228  3.412228  3.412228  ...  0.608252  0.608252  0.608252  0.608252   
3  3.649320  3.649320  3.649320  ...  0.509930  0.509930  0.509930  0.509930   
4  3.762907  3.762907  3.762907  ...  0.522236  0.522236  0.522236  0.522236   

         39        40        41        42        43  44  
0  0.575264  0.575264  0.575264  0.575264  0.575264   5  
1  0.545925  0.545925  0.545925  0.545925  0.545925   2  
2  0.608252  0.608252  0.608252  0.608252  0.608252   1  
3  0.509930  0.509930  0.509930  0.509930  0.509930   4  
4  0.522236  0.522236  0.522236  0.522236  0.522236   1  

[5 rows x 45 columns]

In [169]:
X = resultant_data.iloc[:,:-1]
y = resultant_data.iloc[:,-1]

In [170]:
train_x, test_x, train_y, test_y = train_test_split(X, y, train_size=0.8, random_state = 5)

In [171]:
mul_lr = linear_model.LogisticRegression(multi_class='multinomial', solver='newton-cg')
mul_lr.fit(train_x, train_y)

print("Multinomial Logistic regression Train Accuracy : ", metrics.accuracy_score(train_y, mul_lr.predict(train_x)))
print("Multinomial Logistic regression Test Accuracy : ", metrics.accuracy_score(test_y, mul_lr.predict(test_x)))


Multinomial Logistic regression Train Accuracy :  0.374
Multinomial Logistic regression Test Accuracy :  0.384


In [172]:
rf = RandomForestClassifier(min_samples_leaf=8, n_estimators=60)
rf.fit(train_x, train_y)

print("Multinomial Logistic regression Train Accuracy : ", metrics.accuracy_score(train_y, rf.predict(train_x)))
print("Multinomial Logistic regression Test Accuracy : ", metrics.accuracy_score(test_y, rf.predict(test_x)))

Multinomial Logistic regression Train Accuracy :  0.54925
Multinomial Logistic regression Test Accuracy :  0.366


In [173]:
MODEL_FILE = "../model.pkl"

mdl = rf.fit(X, y)
joblib.dump(mdl, MODEL_FILE)
from sklearn.externals import joblib
